<a href="https://colab.research.google.com/github/WangKehanK/CS505/blob/main/Twitter_User_Gender.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Prediction on age, gender with M3 inference

m3inference

https://github.com/euagendas/m3inference#existing-json-twitter-data

In [1]:
!pip install m3inference

     |████████████████████████████████| 61kB 3.1MB/s 
     |████████████████████████████████| 41.4MB 100kB/s 
  Created wheel for pycld2: filename=pycld2-0.41-cp37-cp37m-linux_x86_64.whl size=9834234 sha256=98cdd789b64a5e1956b22dbd1890d6c9909ace07fe936bd5f5246ad78920b426
  Stored in directory: /root/.cache/pip/wheels/c6/8f/e9/08a1a8932a490175bd140206cd86a3dbcfc70498100de11079
  Created wheel for rauth: filename=rauth-0.7.3-cp37-none-any.whl size=16055 sha256=cdd6560ed378f707d5acb7c51dce4e890bdb40a6a87f5e0b908aa005b7e9a710
  Stored in directory: /root/.cache/pip/wheels/7b/94/5d/81afc278dd5da884a0002563dc4b0fe85f9067a5a40f76f858
Successfully built pycld2 rauth


In [2]:
import numpy as np
import pandas as pd
from m3inference import M3Twitter
import json
import os
import pprint

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
df = pd.read_csv("/content/drive/MyDrive/Twitter_user_handles_to_predict.csv", encoding = "utf-8")
df_labeled = pd.read_csv("/content/drive/My Drive/Twitter_users_labeled_with_age_and_gender.csv", encoding = "latin-1")


In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 25129 entries, 0 to 25128
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   ID        25129 non-null  int64 
 1   Username  25128 non-null  object
dtypes: int64(1), object(1)
memory usage: 392.8+ KB


In [31]:
df_labeled

Unnamed: 0      screen_name  ...  human.labeled.gender human.labeled.age
0              1    _____zac_____  ...                   NaN              23.0
1              2         ___aleia  ...                   NaN              19.0
2              3          ___Dals  ...                     F               NaN
3              4  ___schaeffer___  ...                   NaN              22.0
4              5   __andresiscool  ...                     M               NaN
...          ...              ...  ...                   ...               ...
3275        3276       ZTheBest33  ...                     M               NaN
3276        3277          ztran53  ...                     M               NaN
3277        3278        zupercar1  ...                   NaN              21.0
3278        3279         ZWHITE93  ...                     M               NaN
3279        3280        zzzakari4  ...                   NaN              21.0

[3280 rows x 24 columns]

In [32]:
#convert categories to numbers for human.labeled.gender and lexicon.gender.prediction
from sklearn.preprocessing import LabelEncoder
df_labeled = df_labeled[df_labeled['human.labeled.gender'].notna()]
LE = LabelEncoder()
df_labeled['human.labeled.gender'] = LE.fit_transform(df_labeled['human.labeled.gender'])
df_labeled['lexicon.gender.prediction'] = LE.fit_transform(df_labeled['lexicon.gender.prediction'])

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [33]:
df_labeled

Unnamed: 0      screen_name  ...  human.labeled.gender human.labeled.age
2              3          ___Dals  ...                     0               NaN
4              5   __andresiscool  ...                     1               NaN
5              6  __blowCeeKisses  ...                     0               NaN
6              7          __Bone2  ...                     1               NaN
7              8        __dennisa  ...                     0               NaN
...          ...              ...  ...                   ...               ...
3272        3273      ZoeCalamaco  ...                     0              21.0
3273        3274    zoeynicodemus  ...                     0               NaN
3275        3276       ZTheBest33  ...                     1               NaN
3276        3277          ztran53  ...                     1               NaN
3278        3279         ZWHITE93  ...                     1               NaN

[2144 rows x 24 columns]

In [9]:
df.head()

ID       Username
0   1     JayHolz410
1   2      kelechief
2   3     VicSpencer
3   4  ItsAlexDodson
4   5   xopinkvodka6

In [11]:
user_list = df_labeled['screen_name'].tolist()
#id_list = df_labeled['user_id'].tolist()
print(user_list)
print(len(user_list))

['___Dals', '__andresiscool', '__blowCeeKisses', '__Bone2', '__dennisa', '__greatperhaps', '__KDA_', '__shawtyx3', '_AJoseph_', '_alfiee11', '_amina_r', '_aniyagraham', '_Baaaates724', '_BattsMan_', '_briannadevaux', '_celiaaaxo', '_CoVeRtToWn_', '_dandysandi', '_DemiNeutron', '_dxVi5', '_elisamtz', '_Eric____', '_espibarrera', '_EWillB', '_Fanaticday_', '_FatThor', '_GabiBozeman', '_Gavin0304', '_gilliansummer_', '_GiuliannaTapia', '_haileyevans', '_Huey93', '_ItsLinaa', '_Jaavvii', '_jameshatfield_', '_jaydezha', '_jonstephen', '_kbatch', '_keagannn', '_Kellyann_C', '_Kingdarrion', '_knweedman', '_lexi_lopezz_', '_liamday', '_lilgremlin', '_madisonage', '_maradelgado', '_megodeck', '_moebettaa', '_mvmacita', '_nikkidaniellee', '_notblakegray', '_olisehh', '_PAULWHISKEY', '_reneejoanne', '_rorr_', '_sacredHeart', '_sebas365', '_selgo_', '_tayloralexis13', '_tayshel_2', '_xogloria', '05Panico', '10oso1996', '1DanLawson', '1grn_eyez', '24_archito', '2no_avail', '2raosanjiv', '307cork', 

In [12]:
username = user_list[0] # try one user first, we can loop over the entire user list to get all the user detail
m3cachedir = "drive/MyDrive/cachedir"

if not os.path.exists(m3cachedir):
  os.mkdir(m3cachedir)
pred = []

In [13]:
# initialization
m3twitter=M3Twitter()

# remember to upload Twitter API keys, format as https://github.com/euagendas/m3inference/blob/master/scripts/auth_example.txt
m3twitter.twitter_init_from_file("/content/drive/MyDrive/auth.txt")

# you can also use m3twitter.infer_id(id = "....")
for i in range(0,len(user_list)):
  print(i)
  user_detail = m3twitter.infer_screen_name(user_list[i],skip_cache=True)
  prob_male = user_detail['output']['gender']['male']
  prob_female = user_detail['output']['gender']['female']
  if prob_male > prob_female:
    pred.append('1')
  else:
    pred.append('0')

04/14/2021 20:26:55 - INFO - m3inference.m3inference -   Version 1.1.4
04/14/2021 20:26:55 - INFO - m3inference.m3inference -   Running on cpu.
04/14/2021 20:26:55 - INFO - m3inference.m3inference -   Will use full M3 model.
04/14/2021 20:26:56 - INFO - m3inference.m3inference -   Dir /root/m3/models/ does not exist. Creating now.
04/14/2021 20:26:56 - INFO - m3inference.m3inference -   Dir /root/m3/models/ created.
04/14/2021 20:26:56 - INFO - m3inference.m3inference -   Model full_model does not exist at /root/m3/models/full_model.mdl. Try to download it now.
04/14/2021 20:26:56 - INFO - m3inference.utils -   /root/m3/models/full_model.mdl not found in cache, downloading from https://nlp.stanford.edu/~zijwang/m3inference/full_model.mdl to /tmp/tmpu59l6d86
141007KB [01:11, 1969.41KB/s]                            
04/14/2021 20:28:08 - INFO - m3inference.utils -   Model full_model was downloaded to a tmp file.
04/14/2021 20:28:08 - INFO - m3inference.utils -   Copying tmp file to /root

0


04/14/2021 20:28:10 - INFO - m3inference.dataset -   1 data entries loaded.
Predicting...: 100%|██████████| 1/1 [00:00<00:00,  1.14it/s]
04/14/2021 20:28:11 - INFO - m3inference.m3twitter -   skip_cache is True. Fetching data from Twitter for __andresiscool.
04/14/2021 20:28:11 - INFO - m3inference.m3twitter -   GET /users/show.json?screen_name=__andresiscool
04/14/2021 20:28:11 - INFO - m3inference.dataset -   1 data entries loaded.
Predicting...:   0%|          | 0/1 [00:00<?, ?it/s]

1


Predicting...: 100%|██████████| 1/1 [00:00<00:00,  1.85it/s]
04/14/2021 20:28:11 - INFO - m3inference.m3twitter -   skip_cache is True. Fetching data from Twitter for __blowceekisses.
04/14/2021 20:28:11 - INFO - m3inference.m3twitter -   GET /users/show.json?screen_name=__blowceekisses
04/14/2021 20:28:11 - INFO - m3inference.dataset -   1 data entries loaded.
Predicting...:   0%|          | 0/1 [00:00<?, ?it/s]

...

04/14/2021 20:58:15 - INFO - m3inference.dataset -   1 data entries loaded.
Predicting...: 100%|██████████| 1/1 [00:00<00:00,  1.62it/s]
04/14/2021 20:58:15 - INFO - m3inference.m3twitter -   skip_cache is True. Fetching data from Twitter for ztran53.
04/14/2021 20:58:15 - INFO - m3inference.m3twitter -   GET /users/show.json?screen_name=ztran53


2142


04/14/2021 20:58:16 - INFO - m3inference.dataset -   1 data entries loaded.
Predicting...: 100%|██████████| 1/1 [00:00<00:00,  1.67it/s]
04/14/2021 20:58:16 - INFO - m3inference.m3twitter -   skip_cache is True. Fetching data from Twitter for zwhite93.
04/14/2021 20:58:16 - INFO - m3inference.m3twitter -   GET /users/show.json?screen_name=zwhite93


2143


04/14/2021 20:58:17 - INFO - m3inference.dataset -   1 data entries loaded.
Predicting...: 100%|██████████| 1/1 [00:00<00:00,  1.67it/s]


In [21]:
count = 0
label = df_labeled['human.labeled.gender'].tolist()
for i in range(len(pred)):
  if int(pred[i]) == label[i]:
    count +=1
print('The accuracy for gender prediction using m3inference is', count/len(pred))

The accuracy for gender prediction using m3inference is 0.8311567164179104


In [16]:
count2 = 0
label1 = df_labeled['lexicon.gender.prediction'].tolist()
for i in range(len(label1)):
  if label1[i] == label[i]:
    count2 +=1
print('The accuracy for lexicon.gender.prediction is', count2/len(label1))

The accuracy for lexicon.gender.prediction is 0.7798507462686567


In [38]:
df_labeled = pd.read_csv("/content/drive/My Drive/Twitter_users_labeled_with_age_and_gender.csv", encoding = "latin-1")
df_labeled = df_labeled[df_labeled['human.labeled.gender'].notna()]
df_labeled["gender"] = "M"
count = 0
for index, row in df_labeled.iterrows():
  if pred[count] == '0':
    df_labeled.at[index, 'gender'] = 'F'
  count+=1
df_labeled

Unnamed: 0      screen_name  ...  human.labeled.age gender
2              3          ___Dals  ...                NaN      F
4              5   __andresiscool  ...                NaN      M
5              6  __blowCeeKisses  ...                NaN      F
6              7          __Bone2  ...                NaN      M
7              8        __dennisa  ...                NaN      F
...          ...              ...  ...                ...    ...
3272        3273      ZoeCalamaco  ...               21.0      F
3273        3274    zoeynicodemus  ...                NaN      F
3275        3276       ZTheBest33  ...                NaN      M
3276        3277          ztran53  ...                NaN      M
3278        3279         ZWHITE93  ...                NaN      M

[2144 rows x 25 columns]

In [39]:
df_labeled.to_csv('Twitter_users_labeled_prediction_gender.csv', index=True, header=True)

In [71]:
df_labeled2 = pd.read_csv("/content/drive/My Drive/Twitter_users_labeled_with_age_and_gender.csv", encoding = "latin-1")
df_labeled2 = df_labeled.merge(df_labeled2, how='right')
df_labeled2['gender'] = df_labeled2['gender'].fillna('M')
df_labeled2
df_labeled2.to_csv('Twitter_users_labeled_prediction_gender_allUser.csv', index=True, header=True)

In [5]:
user_list2 = df['Username'].tolist()
print(len(user_list2))
print(user_list2[:10])
m3cachedir = "drive/MyDrive/cachedir"

if not os.path.exists(m3cachedir):
  os.mkdir(m3cachedir)
pred2 = []

25129
['JayHolz410', 'kelechief', 'VicSpencer', 'ItsAlexDodson', 'xopinkvodka6', 'larryislegend', 'gucci1017', 'charles270', 'dirtbaglife', 'TaylorJTakeover']


In [108]:
# initialization
m3twitter=M3Twitter()

# remember to upload Twitter API keys, format as https://github.com/euagendas/m3inference/blob/master/scripts/auth_example.txt
m3twitter.twitter_init_from_file("/content/drive/MyDrive/auth.txt")

# you can also use m3twitter.infer_id(id = "....")
for i in range(13500,len(user_list2)):
  print(i)
  user_detail = m3twitter.infer_screen_name(user_list2[i],skip_cache=True)
  prob_male = user_detail['output']['gender']['male']
  prob_female = user_detail['output']['gender']['female']
  if prob_male > prob_female:
    pred2.append('1')
  else:
    pred2.append('0')
  if i % 500 == 0:
    print('saved')
    with open("/content/drive/My Drive/pred.txt", "wb") as fp:
      pickle.dump(pred2, fp)




Predicting...:   0%|          | 0/1 [00:00<?, ?it/s]

Predicting...: 100%|██████████| 1/1 [00:01<00:00,  1.35s/it]
04/15/2021 05:19:48 - INFO - m3inference.m3twitter -   skip_cache is True. Fetching data from Twitter for _weirdpast_.
04/15/2021 05:19:48 - INFO - m3inference.m3twitter -   GET /users/show.json?screen_name=_weirdpast_
04/15/2021 05:19:48 - INFO - m3inference.dataset -   1 data entries loaded.


Predicting...:   0%|          | 0/1 [00:00<?, ?it/s]

19843




Predicting...: 100%|██████████| 1/1 [00:01<00:00,  1.40s/it]
04/15/2021 05:19:50 - INFO - m3inference.m3twitter -   skip_cache is True. Fetching data from Twitter for bigjairuzi83.
04/15/2021 05:19:50 - INFO - m3inference.m3twitter -   GET /users/show.json?screen_name=bigjairuzi83
04/15/2021 05:19:50 - INFO - m3inference.dataset -   1 data entries loaded.


Predicting...:   0%|          | 0/1 [00:00<?, ?it/s]

19844




Predicting...: 100%|██████████| 1/1 [00:01<00:00,  1.33s/it]
04/15/2021 05:19:51 - INFO - m3inference.m3twitter -   skip_cache is True. Fetching data from Twitter for queenjamesss_.
04/15/2021 05:19:51 - INFO - m3inference.m3twitter -   GET /users/show.json?screen_name=queenjamesss_
04/15/2021 05:19:51 - INFO - m3inference.dataset -   1 data entries loaded.


Predicting...:   0%|          | 0/1 [00:00<?, ?it/s]

...

04/15/2021 06:40:09 - INFO - m3inference.dataset -   1 data entries loaded.


Predicting...:   0%|          | 0/1 [00:00<?, ?it/s]

Predicting...: 100%|██████████| 1/1 [00:01<00:00,  1.24s/it]
04/15/2021 06:40:10 - INFO - m3inference.m3twitter -   skip_cache is True. Fetching data from Twitter for babyymells.
04/15/2021 06:40:10 - INFO - m3inference.m3twitter -   GET /users/show.json?screen_name=babyymells
04/15/2021 06:40:10 - WARNING - m3inference.m3twitter -   Could not retreive screen_name
04/15/2021 06:40:10 - WARNING - m3inference.m3twitter -   Could not retreive id_str
04/15/2021 06:40:10 - WARNING - m3inference.m3twitter -   Could not retreive description
04/15/2021 06:40:10 - WARNING - m3inference.m3twitter -   Could not retreive name
04/15/2021 06:40:10 - WARNING - m3inference.m3twitter -   Could not retreive profile_image_url
04/15/2021 06:40:10 - WARNING - m3inference.m3twitter -   Unable to extract image from Twitter. Using default image.
04/15/2021 06:40:10 - INFO - m3inf

22906




Predicting...: 100%|██████████| 1/1 [00:01<00:00,  1.30s/it]
04/15/2021 06:40:12 - INFO - m3inference.m3twitter -   skip_cache is True. Fetching data from Twitter for _ashtonlang.
04/15/2021 06:40:12 - INFO - m3inference.m3twitter -   GET /users/show.json?screen_name=_ashtonlang
04/15/2021 06:40:12 - WARNING - m3inference.preprocess -   Error fetching profile image from Twitter. HTTP error code was 404.
04/15/2021 06:40:12 - INFO - m3inference.dataset -   1 data entries loaded.


Predicting...:   0%|          | 0/1 [00:00<?, ?it/s]

22907


FileNotFoundError: ignored

In [106]:
print(len(pred2))
print(pred2[-1])
print(pred2[len(pred2)-1])

10671
1
1


In [10]:
import pickle
with open("/content/drive/My Drive/pred.txt", "wb") as fp:
  pickle.dump(pred2, fp)


In [110]:
while True:
  pass

KeyboardInterrupt: ignored

In [11]:
with open("/content/drive/My Drive/pred.txt", "rb") as fp:   # Unpickling
  ls = pickle.load(fp)
print(len(ls))
pred2 = ls[:13500]

13500


In [ ]:
df["gender"] = "male"
for index in range(len(df)):
  if pred2[i] == '0':
    df.at[index, 'gender'] = 'female'

df.head()

In [ ]:
# Get authentication for tweepy from auth.txt
# auth.txt was uploaded before in order to use m3inference
keys = ''
with open(f'auth.txt', 'r') as reader:
  keys=reader.read()
keys = keys.split('\n')
for i in range(len(keys)):
  keys[i] = keys[i].split(':')[1];


In [ ]:
# Setup tweepy
import tweepy
api_key = keys[0]
api_secret = keys[1]
access_token = keys[2]
access_secret = keys[3]
auth = tweepy.OAuthHandler(api_key, api_secret)
auth.set_access_token(access_token, access_secret)
api = tweepy.API(auth, wait_on_rate_limit=True, wait_on_rate_limit_notify=True)


In [ ]:
user2 = user_list2[0]

user = api.get_user(user2)
print(user.name)
print(user.id)
print(user.screen_name)
print(user.description)
from m3inference import get_lang
get_lang(user.description)

Jay Holz
288657952
JayHolz410
The QB at @PositiveVibe410. Management: @DaKidGowie @tate_kobang @joydeangela @RealYGBeats @lorchoc_hd @CharliePeacher @millzdxuglas


'en'

In [ ]:
#!pip install jsonlines
m3twitter=M3Twitter(use_full_model=False)
user_not_found = []
import json
import jsonlines
#len(user_list2[i])
with open('user.jsonl', mode='a') as writer: 
  for i in range(500):
    try:
      user = api.get_user(user_list2[i])
      id = user.id
      name = user.name
      screen_name = user.screen_name
      description = user.description
      lang = get_lang(user.description)
      input = {"id": str(id), "name": name, "screen_name": screen_name, "description": description, "lang":lang}
      writer.write(input)
    except tweepy.TweepError as e:
      user_not_found.append(user_list2[i])
      pass



04/12/2021 17:33:37 - INFO - m3inference.m3inference -   Version 1.1.4
04/12/2021 17:33:37 - INFO - m3inference.m3inference -   Running on cpu.
04/12/2021 17:33:37 - INFO - m3inference.m3inference -   Will use text model. Note that as M3 was optimized to work well with both image and text data,                                     it is not recommended to use text only model unless you do not have the profile image.
04/12/2021 17:33:37 - INFO - m3inference.m3inference -   Model text_model exists at /root/m3/models/text_model.mdl.
04/12/2021 17:33:37 - INFO - m3inference.utils -   Checking MD5 for model text_model at /root/m3/models/text_model.mdl
04/12/2021 17:33:37 - INFO - m3inference.utils -   MD5s match.
04/12/2021 17:33:37 - INFO - m3inference.m3inference -   Loaded pretrained weight at /root/m3/models/text_model.mdl
Exception ignored in: <function _ConnectionBase.__del__ at 0x7f415950e8c0>
Traceback (most recent call last):
  File "/usr/lib/python3.7/multiprocessing/connection.py"

In [ ]:
user_info = m3twitter.infer('user.jsonl') #Same method as M3Inference.infer(...)
list_user_info = []
for k,v in user_info.items():
  list_user_info.append(v['gender'])
print(len(list_user_info)+len(user_not_found))

04/12/2021 17:24:27 - INFO - m3inference.dataset -   272 data entries loaded.
/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py:477: UserWarning: This DataLoader will create 4 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  cpuset_checked))

Predicting...: 100%|██████████| 17/17 [00:03<00:00,  5.33it/s]

380


In [ ]:
# Create new column to save the predicted value
print(user)
print(len(list_user_info)+len(user_not_found))
df["gender"] = "male"
print(df.at[0, 'Username'] in user_not_found)
print(len(user_not_found))
print(len(list_user_info))
print(user_not_found[-10:])
user = api.get_user('KillWillBeats')
user

earlxsweat
380
False
108
272
['Michael_Tesone', 'paradox0329', 'tolucrixus', 'Childish_Dick', 'abrigw', 'Trugvme', 'ghostboy_jaysee', 'dubstepsmash1', 'mixmixup1', 'moneyymaurice']


User(_api=<tweepy.api.API object at 0x7f4153fe1050>, _json={'id': 23256441, 'id_str': '23256441', 'name': 'kill will did the track', 'screen_name': 'KillWillBeats', 'location': "Cincinnati, but I'm EVERYWHERE", 'profile_location': None, 'description': 'TBN', 'url': 'https://t.co/jGVeWh1x4n', 'entities': {'url': {'urls': [{'url': 'https://t.co/jGVeWh1x4n', 'expanded_url': 'http://www.thoroughbynature.com', 'display_url': 'thoroughbynature.com', 'indices': [0, 23]}]}, 'description': {'urls': []}}, 'protected': False, 'followers_count': 6525, 'friends_count': 4375, 'listed_count': 69, 'created_at': 'Sun Mar 08 00:41:54 +0000 2009', 'favourites_count': 6715, 'utc_offset': None, 'time_zone': None, 'geo_enabled': True, 'verified': False, 'statuses_count': 19049, 'lang': None, 'status': {'created_at': 'Sat Apr 10 01:18:49 +0000 2021', 'id': 1380691707843342336, 'id_str': '1380691707843342336', 'text': 'RT @1future: DMX FOREVER LEGENDARY...', 'truncated': False, 'entities': {'hashtags': [], 's

In [ ]:
# Loop over each row to assign the predict value, should be used with M3
count = 0

for index in range(len(df)):
    if df.at[index, 'Username'] not in user_not_found:
      gender_info = list_user_info[count]
      prob_male = gender_info['male']
      prob_female = gender_info['female']
      if prob_male > prob_female:
        df.at[index, 'gender'] = 'male'
      else:
        df.at[index, 'gender'] = 'female'
      count +=1
    else:
      df.at[index, 'gender'] = None

['TheDailyOoze']


In [ ]:
df

ID        Username  gender
0          1      JayHolz410    male
1          2       kelechief    male
2          3      VicSpencer    male
3          4   ItsAlexDodson  female
4          5    xopinkvodka6  female
...      ...             ...     ...
25124  25125          13luvr    male
25125  25126         Racetac    male
25126  25127  MrNoFilter_100    male
25127  25128    OgheneNerojr    male
25128  25129      earlxsweat    male

[25129 rows x 3 columns]